# Library and Global Variables

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from collections import defaultdict
import sys
import matplotlib.pyplot as plt
from tqdm import tqdm

In [2]:
sys.path.insert(0, '..') # to access the module one level up

In [3]:
from Transliterate.transliterate.utils.vowels import Vowels

In [4]:
VOWELS = Vowels().all_vowels

def isVowel(char: str) -> bool: 
    if char[-1] in ['2', '3', '4', '5']: # handle the tonations
        char = char[:-1]
    return char in VOWELS

# Preparing the Methods


In [5]:
def prepare_bi_phonemes(csv_path: str) -> defaultdict:

    df = pd.read_csv(csv_path)
    bi_phonemes = []

    for index, row in tqdm(df.iterrows()):
        thai_phonemes = row['thai phoneme'].split(' ')
        thai_phonemes = [ph for ph in thai_phonemes if ph != '_']
        
        for i in range(len(thai_phonemes) - 1):
            current_phoneme = thai_phonemes[i]
            next_phoneme = thai_phonemes[i + 1]
            eos = True

            if i != len(thai_phonemes) - 2:
                eos = False
                next_next_phoneme = thai_phonemes[i + 2]

            if not isVowel(current_phoneme):
                if isVowel(next_phoneme):
                    bi_phonemes.append((current_phoneme, next_phoneme))
            else:
                if not eos:
                    if not isVowel(next_phoneme) and not isVowel(next_next_phoneme):
                        bi_phonemes.append((current_phoneme, next_phoneme))
                else:
                    if not isVowel(next_phoneme):
                        bi_phonemes.append((current_phoneme, next_phoneme))

    return bi_phonemes

def get_tri_phonemes(csv_path: str, show_results=False) -> defaultdict:

    bi_phonemes = prepare_bi_phonemes(csv_path)
    tri_phonemes = defaultdict(int)

    last_tri_phoneme = []
    for bi_phoneme in bi_phonemes:
        initial, final = bi_phoneme
        if len(last_tri_phoneme) == 0:
            last_tri_phoneme.append(initial)
            last_tri_phoneme.append(final)

        elif isVowel(initial):
            last_tri_phoneme.append(final)
            tri_phonemes[tuple(last_tri_phoneme)] += 1
            last_tri_phoneme = []

        else:
            last_tri_phoneme.append('')
            tri_phonemes[tuple(last_tri_phoneme)] += 1
            last_tri_phoneme = [initial, final]

    if len(last_tri_phoneme) == 2:
        last_tri_phoneme.append('')
        tri_phonemes[tuple(last_tri_phoneme)] += 1

    if len(last_tri_phoneme) == 3:
        tri_phonemes[tuple(last_tri_phoneme)] += 1

    if show_results:
        for trigram, count in tri_phonemes.items():
            print(f"{trigram}: {count}")

        print(f"Total tri-phonemes: {sum(tri_phonemes.values())}")
    
    return tri_phonemes

def unknown_tri_phonemes(tri_phonemes1: defaultdict, tri_phonemes2: defaultdict) -> list:
    unknown = []
    for phoneme in tri_phonemes1.keys():
        if phoneme not in tri_phonemes2.keys():
            unknown.append(phoneme)

    return unknown
    
def compare_tri_phonemes(tri_phonemes1: defaultdict, title_1: str , tri_phonemes2: defaultdict, title_2: str) -> None:
    tri_phonemes2 = {k: v for k, v in sorted(tri_phonemes2.items(), key=lambda item: item[1], reverse=True)}
    total_tri_phonemes = list(tri_phonemes2.keys()) + unknown_tri_phonemes(tri_phonemes1, tri_phonemes2)

    tri_phonemes_1_counts = [tri_phonemes1.get(ph, 0) for ph in total_tri_phonemes]
    tri_phonemes_2_counts = [tri_phonemes2.get(ph, 0) for ph in total_tri_phonemes]   

    np_tri_phonemes1_counts = np.array(tri_phonemes_1_counts) / sum(tri_phonemes_1_counts)
    np_tri_phonemes2_counts = np.array(tri_phonemes_2_counts) / sum(tri_phonemes_2_counts)

    index = np.arange(len(total_tri_phonemes))
    bar_height = 0.8
    fig_height = len(total_tri_phonemes) * bar_height * 0.2
    fig, ax = plt.subplots(figsize=(10, fig_height))

    bar1 = ax.barh(index, np_tri_phonemes1_counts, bar_height, color='mediumturquoise', label=title_1)
    ax.plot(np_tri_phonemes2_counts, index, color='crimson', label=title_2)
    ax.set_title('Tri-Phoneme Distributions Comparison')
    ax.set_xlabel('Count')
    ax.set_ylabel('Tri-Phonemes')
    ax.set_yticks(index)
    ax.set_yticklabels(total_tri_phonemes, fontsize=10)
    ax.legend()

    plt.subplots_adjust(left=0.2, right=0.95, top=0.9, bottom=0.1)
    plt.tight_layout()
    plt.savefig('./ThaiTriPhonemesDistribution.png', bbox_inches='tight')
    plt.show()


In [6]:
generated_path = '../generated/processed/combined_sentences_with_phoneme.csv'
tsync2_path = '../tsync2/processed/combined_tsync2_thai_sentences_phoneme.csv'

generated_tri_phonemes = get_tri_phonemes(generated_path, show_results=False)
tsync2_tri_phonemes = get_tri_phonemes(tsync2_path, show_results=False)

2025it [00:00, 9521.08it/s]
2710it [00:00, 9767.26it/s] 


In [7]:
print(f"Generated tri-phonemes: {len(generated_tri_phonemes)}")
print(f"Tsync2 tri-phonemes: {len(tsync2_tri_phonemes)}")

Generated tri-phonemes: 1136
Tsync2 tri-phonemes: 3752


# Plot the Distributions

In [8]:
compare_tri_phonemes(generated_tri_phonemes, 'Generated', tsync2_tri_phonemes, 'Tsync2')

# Check the Non-existing Phonemes

In [9]:
print(f'In Generated but not in Tsync2: {unknown_tri_phonemes(generated_tri_phonemes, tsync2_tri_phonemes)}')
print(f'In Tsync2 but not in Generated: {unknown_tri_phonemes(tsync2_tri_phonemes, generated_tri_phonemes)}')

In Generated but not in Tsync2: [('d', 'ɯː2', 'n'), ('n', 'aː5', 'n'), ('p', 'iːa', ''), ('cʰ', 'i', 'm'), ('l', 'aː4', ''), ('pʰl', 'i4', ''), ('w', 'i', 'w'), ('tʰ', 'ᴐː4', 'n'), ('j', 'a3', 'ŋ'), ('w', 'o', 'n'), ('l', 'a4', 'p'), ('d', 'a3', 'ŋ'), ('r', 'u4', 'ŋ'), ('kʰ', 'a3', 'm'), ('p', 'a', 'ŋ'), ('j', 'ɯː', 'm'), ('b', 'aː2', 'j'), ('kr', 'iː', 'm'), ('cʰ', 'ᴐː4', 'p'), ('tr', 'iː2', 't'), ('ŋ', 'u2', 'n'), ('j', 'u2', 'n'), ('f', 'ɛː4', 'n'), ('l', 'iː2', 'k'), ('p', 'ᴐ2', 'p'), ('w', 'aː3', 'j'), ('c', 'eː2', 'k'), ('s', 'ᴐː5', 'j'), ('h', 'uːa5', 'n'), ('cʰ', 'ᴐ4', 'k'), ('l', 'ɛː4', 't'), ('t', 'ɛː', 'm'), ('pʰ', 'i', 'ŋ'), ('n', 'e2', 't'), ('n', 'ᴐ4', 'k'), ('pʰ', 'oː5', 'n'), ('m', 'ᴐː5', 'n'), ('c', 'i2', 'p'), ('tr', 'iː', 'm'), ('pr', 'a2', 't'), ('j', 'a5', 'n'), ('p', 'ɛː', 'm'), ('cʰ', 'iːa3', 'w'), ('l', 'ɯːa', 'n'), ('s', 'ɤː3', 'p'), ('l', 'ɯːa3', 'ŋ'), ('j', 'ᴐː3', 'm'), ('j', 'ᴐː2', 'm'), ('n', 'iː3', 't'), ('ʔ', 'ɤː', 'n'), ('pr', 'o2', 'p'), ('pʰ', 'ɛ4', 'k